### An engineering problem from "Engineering Optimization" by Xin-She Yang

Goal: Design an optimal spring (cheapest / least material needed) that does the job. Parameters we can change: $d$, the diameter of the coil; $L$, the length of the spring; $w$, the thickness of the wire.

Task: Minimize $$(2+L)dw^2$$ subject to the constraints
\begin{align*}
g_1(L,d,w) &= 1 - \frac{d^3L}{7178w^4} \leq 0\\[5pt]
g_2(L,d,w) &= \frac{4d^2 - wd}{12566dw^3 - w^4} + \frac{1}{5108w^2} - 1 \leq 0\\[5pt]
g_3(L,d,w) &= 1 - \frac{140.45w}{d^2L} \leq 0\\[5pt]
g_4(L,d,w) &= \frac{w+d}{1.5} - 1 \leq 0
\end{align*}
with boundary conditions
$$
0.05 \leq w \leq 2.0
\qquad\qquad
0.25 \leq d \leq 1.3
\qquad\qquad
2.0 \leq L \leq 15.0
$$

In [1]:
import math
import random

In [2]:
def random_in_range(lower, upper):
    return random.random() * (upper - lower) + lower

In [3]:
def g1(L,d,w):
    return 1 - d**3 * L / (7178 * w**4)

def g2(L,d,w):
    return (4*d**2 - w*d)/(12566 * d * w**3 - w**4) + 1/(5108*w**2) - 1

def g3(L,d,w):
    return 1 - 140.45 * w / (d**2*L)

def g4(L,d,w):
    return (w+d)/1.5 - 1

def satisfies_constraints(L,d,w):
    return g1(L,d,w) <= 0 and g2(L,d,w) <= 0 and g3(L,d,w) <= 0 and g4(L,d,w) <= 0

In [4]:
def score(L,d,w):
    return (2+L)*d*w**2

In [5]:
def tweak(L,d,w):
    delta_w = 0.01
    delta_d = 0.01
    delta_L = 0.1
    
    new_w = w + random_in_range(-1, 1) * delta_w
    while new_w < 0.05 or new_w > 2:
        new_w = w + random_in_range(-1, 1) * delta_w
    
    new_d = d + random_in_range(-1, 1) * delta_d
    while new_d < 0.25 or new_d > 1.3:
        new_d = d + random_in_range(-1, 1) * delta_d
        
    new_L = L + random_in_range(-1, 1) * delta_L
    while new_L < 2 or new_L > 15:
        new_L = L + random_in_range(-1, 1) * delta_L
        
    return (new_L, new_d, new_w)
        
tweak(4, .6, 1.5)

(4.049297386377984, 0.6001116306400456, 1.497565704133333)

In [6]:
def random_solution():
    return (
        random_in_range(2, 15),
        random_in_range(0.25, 1.3),
        random_in_range(0.05, 2),
    )

In [7]:
def hill_climbing():
    
    start = random_solution()
    while not satisfies_constraints(*start):
#         print(g1(*start), g2(*start), g3(*start), g4(*start))
        start = random_solution()
    sol = start
    value = score(*sol)

    bad = 0
    while True:
#         print(sol)
        new_sol = tweak(*sol)
        while not satisfies_constraints(*new_sol):
            new_sol = tweak(*sol)
        new_value = score(*new_sol)
        if new_value < value:
            bad = 0
            sol = new_sol
            value = new_value
        else:
            bad += 1
            if bad > 1000:
                print(value)
                return sol
    


In [19]:
#sol = hill_climbing()
sol = [2.02310938, 0.25113418, 0.05218225]
print(sol)
print(g1(*sol), g2(*sol), g3(*sol), g4(*sol))
print(score(*sol))

[2.02310938, 0.25113418, 0.05218225]
0.3979366633812622 -0.39471975579066854 -56.43988085042353 -0.7977890466666667
0.0027511436522230925


In [221]:
# 0.0028274

In [ ]:
# 0.009314798606469854

In [19]:
# smarter: sample 1000 tweaks to find a good initial_temp that gives a desired p_0
# or: heat the system slowly until the % of worsening solutions is what you want
initial_temp = 0.005
alpha = 0.999
final_temp = initial_temp / 10000
trials_per_temp = 1000

start = random_solution()
while not satisfies_constraints(*start):
    start = random_solution()
sol = start
value = score(*sol)

In [20]:
temp = initial_temp
generation = 0
best_sol = None
best_score = None

while temp >= final_temp:
    generation += 1
    accepted_worse = 0
    total_worse = 0
    for i in range(trials_per_temp):
        new_sol = tweak(*sol)
        while not satisfies_constraints(*new_sol):
            new_sol = tweak(*sol)

        new_value = score(*new_sol)
        
        delta = new_value - value
        delta *= -1
        if delta >= 0:
            sol = new_sol
            value = new_value
            if best_score is None or value < best_score:
                best_sol = sol
                best_score = value
        else:
            total_worse += 1
            p = math.exp(delta/temp)
            r = random.random()
            if r <= p:
                accepted_worse += 1
                sol = new_sol
                value = new_value

    print(
        f"Gen #{generation}: temp = {temp:.6f}, "
        f"best score = {best_score:.8f}, "
        f"cur score = {value:.8f}, "
        f"worse accepted = {round(accepted_worse/total_worse*100,2):.2f}%"
    )
    temp = temp * alpha
    


Gen #1: temp = 0.005000, best score = 0.03340431, cur score = 0.03469792, worse accepted = 38.71%
Gen #2: temp = 0.004995, best score = 0.02719822, cur score = 0.04007922, worse accepted = 42.56%
Gen #3: temp = 0.004990, best score = 0.01912221, cur score = 0.02170816, worse accepted = 43.12%
Gen #4: temp = 0.004985, best score = 0.00812235, cur score = 0.01227239, worse accepted = 60.06%
Gen #5: temp = 0.004980, best score = 0.00564729, cur score = 0.01122452, worse accepted = 73.52%
Gen #6: temp = 0.004975, best score = 0.00564729, cur score = 0.01093423, worse accepted = 70.80%
Gen #7: temp = 0.004970, best score = 0.00564729, cur score = 0.01795741, worse accepted = 63.41%
Gen #8: temp = 0.004965, best score = 0.00564729, cur score = 0.01828137, worse accepted = 65.35%
Gen #9: temp = 0.004960, best score = 0.00426376, cur score = 0.00491609, worse accepted = 76.23%
Gen #10: temp = 0.004955, best score = 0.00426376, cur score = 0.01098171, worse accepted = 78.37%
Gen #11: temp = 0.0

Gen #124: temp = 0.004421, best score = 0.00302071, cur score = 0.00899644, worse accepted = 63.33%
Gen #125: temp = 0.004417, best score = 0.00302071, cur score = 0.01016040, worse accepted = 80.87%
Gen #126: temp = 0.004412, best score = 0.00302071, cur score = 0.01509471, worse accepted = 78.66%
Gen #127: temp = 0.004408, best score = 0.00302071, cur score = 0.00567877, worse accepted = 74.55%
Gen #128: temp = 0.004403, best score = 0.00302071, cur score = 0.00733874, worse accepted = 78.79%
Gen #129: temp = 0.004399, best score = 0.00302071, cur score = 0.02124405, worse accepted = 66.94%
Gen #130: temp = 0.004395, best score = 0.00302071, cur score = 0.01383536, worse accepted = 65.33%
Gen #131: temp = 0.004390, best score = 0.00302071, cur score = 0.00524801, worse accepted = 75.31%
Gen #132: temp = 0.004386, best score = 0.00302071, cur score = 0.00628919, worse accepted = 73.43%
Gen #133: temp = 0.004381, best score = 0.00302071, cur score = 0.01826559, worse accepted = 64.75%


Gen #231: temp = 0.003972, best score = 0.00302071, cur score = 0.01367172, worse accepted = 71.36%
Gen #232: temp = 0.003968, best score = 0.00302071, cur score = 0.00840734, worse accepted = 64.70%
Gen #233: temp = 0.003964, best score = 0.00302071, cur score = 0.00669280, worse accepted = 70.23%
Gen #234: temp = 0.003960, best score = 0.00302071, cur score = 0.01121305, worse accepted = 76.79%
Gen #235: temp = 0.003956, best score = 0.00302071, cur score = 0.01671034, worse accepted = 61.56%
Gen #236: temp = 0.003952, best score = 0.00302071, cur score = 0.00809916, worse accepted = 62.18%
Gen #237: temp = 0.003948, best score = 0.00302071, cur score = 0.00729762, worse accepted = 71.28%
Gen #238: temp = 0.003944, best score = 0.00302071, cur score = 0.00691382, worse accepted = 74.13%
Gen #239: temp = 0.003941, best score = 0.00302071, cur score = 0.01655303, worse accepted = 64.91%
Gen #240: temp = 0.003937, best score = 0.00302071, cur score = 0.01609734, worse accepted = 58.01%


Gen #341: temp = 0.003558, best score = 0.00299743, cur score = 0.01005335, worse accepted = 67.00%
Gen #342: temp = 0.003555, best score = 0.00299743, cur score = 0.01652854, worse accepted = 50.52%
Gen #343: temp = 0.003551, best score = 0.00299743, cur score = 0.00539595, worse accepted = 65.85%
Gen #344: temp = 0.003548, best score = 0.00299743, cur score = 0.00686337, worse accepted = 74.69%
Gen #345: temp = 0.003544, best score = 0.00299743, cur score = 0.00533974, worse accepted = 72.82%
Gen #346: temp = 0.003540, best score = 0.00299743, cur score = 0.00595562, worse accepted = 73.14%
Gen #347: temp = 0.003537, best score = 0.00299743, cur score = 0.01001887, worse accepted = 68.55%
Gen #348: temp = 0.003533, best score = 0.00299743, cur score = 0.01444194, worse accepted = 60.86%
Gen #349: temp = 0.003530, best score = 0.00299743, cur score = 0.00850975, worse accepted = 71.55%
Gen #350: temp = 0.003526, best score = 0.00299743, cur score = 0.00553286, worse accepted = 74.91%


Gen #453: temp = 0.003181, best score = 0.00291015, cur score = 0.00659253, worse accepted = 70.44%
Gen #454: temp = 0.003178, best score = 0.00291015, cur score = 0.00684746, worse accepted = 69.50%
Gen #455: temp = 0.003175, best score = 0.00291015, cur score = 0.00770002, worse accepted = 74.73%
Gen #456: temp = 0.003172, best score = 0.00291015, cur score = 0.00519677, worse accepted = 76.47%
Gen #457: temp = 0.003168, best score = 0.00291015, cur score = 0.00412759, worse accepted = 77.41%
Gen #458: temp = 0.003165, best score = 0.00291015, cur score = 0.00842282, worse accepted = 75.95%
Gen #459: temp = 0.003162, best score = 0.00291015, cur score = 0.01379421, worse accepted = 65.95%
Gen #460: temp = 0.003159, best score = 0.00291015, cur score = 0.01404098, worse accepted = 53.51%
Gen #461: temp = 0.003156, best score = 0.00291015, cur score = 0.01030295, worse accepted = 46.73%
Gen #462: temp = 0.003153, best score = 0.00291015, cur score = 0.01855465, worse accepted = 50.30%


...

Gen #8857: temp = 0.000001, best score = 0.00282109, cur score = 0.00282390, worse accepted = 0.00%
Gen #8858: temp = 0.000001, best score = 0.00282109, cur score = 0.00282390, worse accepted = 0.00%
Gen #8859: temp = 0.000001, best score = 0.00282109, cur score = 0.00282390, worse accepted = 0.00%
Gen #8860: temp = 0.000001, best score = 0.00282109, cur score = 0.00282390, worse accepted = 0.00%
Gen #8861: temp = 0.000001, best score = 0.00282109, cur score = 0.00282390, worse accepted = 0.00%
Gen #8862: temp = 0.000001, best score = 0.00282109, cur score = 0.00282390, worse accepted = 0.00%
Gen #8863: temp = 0.000001, best score = 0.00282109, cur score = 0.00282299, worse accepted = 0.00%
Gen #8864: temp = 0.000001, best score = 0.00282109, cur score = 0.00282299, worse accepted = 0.00%
Gen #8865: temp = 0.000001, best score = 0.00282109, cur score = 0.00282299, worse accepted = 0.00%
Gen #8866: temp = 0.000001, best score = 0.00282109, cur score = 0.00282299, worse accepted = 0.00%


Gen #8940: temp = 0.000001, best score = 0.00282109, cur score = 0.00282285, worse accepted = 0.00%
Gen #8941: temp = 0.000001, best score = 0.00282109, cur score = 0.00282285, worse accepted = 0.00%
Gen #8942: temp = 0.000001, best score = 0.00282109, cur score = 0.00282285, worse accepted = 0.00%
Gen #8943: temp = 0.000001, best score = 0.00282109, cur score = 0.00282285, worse accepted = 0.00%
Gen #8944: temp = 0.000001, best score = 0.00282109, cur score = 0.00282285, worse accepted = 0.00%
Gen #8945: temp = 0.000001, best score = 0.00282109, cur score = 0.00282285, worse accepted = 0.00%
Gen #8946: temp = 0.000001, best score = 0.00282109, cur score = 0.00282285, worse accepted = 0.00%
Gen #8947: temp = 0.000001, best score = 0.00282109, cur score = 0.00282285, worse accepted = 0.00%
Gen #8948: temp = 0.000001, best score = 0.00282109, cur score = 0.00282285, worse accepted = 0.00%
Gen #8949: temp = 0.000001, best score = 0.00282109, cur score = 0.00282285, worse accepted = 0.00%


Gen #9027: temp = 0.000001, best score = 0.00282109, cur score = 0.00282145, worse accepted = 0.00%
Gen #9028: temp = 0.000001, best score = 0.00282109, cur score = 0.00282145, worse accepted = 0.00%
Gen #9029: temp = 0.000001, best score = 0.00282109, cur score = 0.00282145, worse accepted = 0.00%
Gen #9030: temp = 0.000001, best score = 0.00282109, cur score = 0.00282145, worse accepted = 0.00%
Gen #9031: temp = 0.000001, best score = 0.00282109, cur score = 0.00282145, worse accepted = 0.00%
Gen #9032: temp = 0.000001, best score = 0.00282109, cur score = 0.00282145, worse accepted = 0.00%
Gen #9033: temp = 0.000001, best score = 0.00282109, cur score = 0.00282145, worse accepted = 0.00%
Gen #9034: temp = 0.000001, best score = 0.00282109, cur score = 0.00282145, worse accepted = 0.00%
Gen #9035: temp = 0.000001, best score = 0.00282109, cur score = 0.00282145, worse accepted = 0.00%
Gen #9036: temp = 0.000001, best score = 0.00282109, cur score = 0.00282145, worse accepted = 0.00%


Gen #9111: temp = 0.000001, best score = 0.00282109, cur score = 0.00282145, worse accepted = 0.00%
Gen #9112: temp = 0.000001, best score = 0.00282109, cur score = 0.00282145, worse accepted = 0.00%
Gen #9113: temp = 0.000001, best score = 0.00282109, cur score = 0.00282145, worse accepted = 0.00%
Gen #9114: temp = 0.000001, best score = 0.00282109, cur score = 0.00282145, worse accepted = 0.00%
Gen #9115: temp = 0.000001, best score = 0.00282109, cur score = 0.00282145, worse accepted = 0.00%
Gen #9116: temp = 0.000001, best score = 0.00282109, cur score = 0.00282145, worse accepted = 0.00%
Gen #9117: temp = 0.000001, best score = 0.00282109, cur score = 0.00282145, worse accepted = 0.00%
Gen #9118: temp = 0.000001, best score = 0.00282109, cur score = 0.00282145, worse accepted = 0.00%
Gen #9119: temp = 0.000001, best score = 0.00282109, cur score = 0.00282145, worse accepted = 0.00%
Gen #9120: temp = 0.000001, best score = 0.00282109, cur score = 0.00282145, worse accepted = 0.00%


Gen #9196: temp = 0.000001, best score = 0.00282109, cur score = 0.00282145, worse accepted = 0.00%
Gen #9197: temp = 0.000001, best score = 0.00282109, cur score = 0.00282145, worse accepted = 0.00%
Gen #9198: temp = 0.000001, best score = 0.00282109, cur score = 0.00282145, worse accepted = 0.00%
Gen #9199: temp = 0.000001, best score = 0.00282109, cur score = 0.00282145, worse accepted = 0.00%
Gen #9200: temp = 0.000001, best score = 0.00282109, cur score = 0.00282145, worse accepted = 0.00%
Gen #9201: temp = 0.000001, best score = 0.00282109, cur score = 0.00282145, worse accepted = 0.00%
Gen #9202: temp = 0.000001, best score = 0.00282109, cur score = 0.00282145, worse accepted = 0.00%
Gen #9203: temp = 0.000001, best score = 0.00282109, cur score = 0.00282145, worse accepted = 0.00%
Gen #9204: temp = 0.000001, best score = 0.00282109, cur score = 0.00282145, worse accepted = 0.00%
Gen #9205: temp = 0.000001, best score = 0.00282109, cur score = 0.00282145, worse accepted = 0.00%


In [21]:
best_sol

(2.0009006497680337, 0.28201641967204255, 0.05000261046657898)

In [22]:
sol = best_sol
print(g1(*sol), g2(*sol), g3(*sol), g4(*sol))

-0.0001716575880703619 -0.2354609392842808 -43.13062790855916 -0.7786539799075857


In [23]:
score(*sol)

0.0028210937435474443